In [1]:
import requests
import sqlite3
import datetime
from bs4 import BeautifulSoup

con = sqlite3.connect("cafe.db")
cur = con.cursor()
cur.execute('select * from data where type is "1"')
schizophrenia_free = cur.fetchall()
cur.execute('select * from data where type is "2"')
schizophrenia_qna = cur.fetchall()
cur.execute('select * from data where type is "3"')
adhd_free = cur.fetchall()
cur.execute('select * from data where type is "4"')
adhd_anonymous = cur.fetchall()
con.commit()
con.close()

con = sqlite3.connect("cafe_data.db")
cur = con.cursor()
cur.execute('select * from data where category is "1"')
sad = cur.fetchall()
con.commit()
con.close()

In [2]:
con = sqlite3.connect("raw_data.db")
cur = con.cursor()

cur.execute('select * from data where category is "5"')
freeboard = cur.fetchall()

con.commit()
con.close()

In [5]:
print("조현병-자유게시판:" + str(len(schizophrenia_free)))
print("조현병-상담실:" + str(len(schizophrenia_qna)))
print("ADHD-자유게시판:" + str(len(adhd_free)))
print("ADHD-익명게시판:" + str(len(adhd_anonymous)))
print("우울증-자유게시판:" + str(len(sad)))

조현병-자유게시판:2360
조현병-상담실:11364
ADHD-자유게시판:1390
ADHD-익명게시판:3727
우울증-자유게시판:9855


In [6]:
print("일반 자유게시판:" + str(len(freeboard)))

일반 자유게시판:7845


In [3]:
schizophrenia = schizophrenia_free + schizophrenia_qna
adhd = adhd_free + adhd_anonymous

## Sen2Vec

In [4]:
import sen2vec
sen2vec = sen2vec.Sentence2Vec()
sad_list = []
sad_list = sen2vec.get_vector(sad)

C:\anaconda3\lib\site-packages\gensim\utils.py:1212: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [5]:
import sen2vec
sen2vec = sen2vec.Sentence2Vec()
adhd_list = []
adhd_list = sen2vec.get_vector(adhd)

In [6]:
import sen2vec
sen2vec = sen2vec.Sentence2Vec()
schizophrenia_list = []
schizophrenia_list = sen2vec.get_vector(schizophrenia)

In [7]:
import sen2vec
sen2vec = sen2vec.Sentence2Vec()
freeboard_list = []
freeboard_list = sen2vec.get_vector(freeboard)

### 정신분열증

In [8]:
x_train = []
for i in range(0,len(schizophrenia_list),1):
    x_train.append(schizophrenia_list[i])
for i in range(0,len(freeboard_list),1):
    x_train.append(freeboard_list[i])

In [9]:
y_train = []
for i in range(0,len(schizophrenia_list),1):
    y_train.append(0)
for i in range(0,len(freeboard_list),1):
    y_train.append(1)

### ADHD

In [40]:
x_train = []
for i in range(0,len(adhd_list),1):
    x_train.append(adhd_list[i])
for i in range(0,len(freeboard_list),1):
    x_train.append(freeboard_list[i])

In [41]:
y_train = []
for i in range(0,len(adhd_list),1):
    y_train.append(0)
for i in range(0,len(freeboard_list),1):
    y_train.append(1)

### 우울증

In [29]:
x_train = []
for i in range(0,len(sad_list),1):
    x_train.append(sad_list[i])
for i in range(0,len(freeboard_list),1):
    x_train.append(freeboard_list[i])

In [30]:
y_train = []
for i in range(0,len(sad_list),1):
    y_train.append(0)
for i in range(0,len(freeboard_list),1):
    y_train.append(1)

여기까지 vector

### SVM

- 정신분열증

In [10]:
from sklearn.svm import SVC
ml = SVC(kernel='linear', C=1.0, random_state=0, probability=True)
ml.fit(x_train,y_train)

SVC(C=1.0, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto', kernel='linear',
  max_iter=-1, probability=True, random_state=0, shrinking=True, tol=0.001,
  verbose=False)

In [11]:
y_pred = ml.predict(x_train)
y_pred_prob = ml.predict_proba(x_train)

In [13]:
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
print('총 테스트 개수: %d, 오류개수: %d' %(len(y_train), (y_train != y_pred).sum()))
print('정확도: %.2f' %accuracy_score(y_train, y_pred))
print('f1_score : %.2f' %f1_score(y_train, y_pred, average='macro'))

총 테스트 개수: 21825, 오류개수: 1998
정확도: 0.91
f1_score : 0.91


In [ ]:
for i in range(0,len(y_pred_prob),1):
    print(y_pred_prob[i], schizophrenia[i][2])
for i in range(0,100,1):
    print(y_pred_prob[i], schizophrenia[i][2])

[0.24741861 0.75258139] 오늘 psyfree 님의 카페가 개설되었는데 하루도 안되어 이렇게 많은 방문자가 있는 줄은...
저는 지인을 통해서 처음 가입하게 되었는데요.  이렇게 많은 분들이 함께하고 있는지 몰랐네요.
psyfree 님과 모두 함께 이겨나가면 좋겠어요.
화이팅!
[0.79949019 0.20050981] 더도 덜도 말고 한가위만 같아라 


넉넉한 마음으로 정도 나누고 사랑도 나누는
우리의 최대 명절 추석입니다

정겨운 얼굴이 기다리는 고향에 가실 때는
손에 손에, 마음과 마음에 사랑 가득 담아 가시고
삶의 보금자리로 돌아오시는 길에는
웃음 보따리에는 웃음 가득
행복 보따리에는 행복 가득 담아오시는 
풍요로운 추석 여유로운 추석 되시기 바랍니다

올 추석에는
하늘엔 둥근 보름달이
우리에겐 사랑의 보름달이
그리고 세상에는 둥근 情이 뜨게 하소서.
 
 
 
[0.08503748 0.91496252] ㅋㅋ
히히
 
[0.08340271 0.91659729]     웃자고요.
[0.88558299 0.11441701] 따뜻한 의사에 반해.... 미 80대 환자 480억 기부
  http://joongang.joinsmsn.com/article/802/6263802.html?ctg= 정현목 기자
  경쟁과 욕심 속에서 사람사는 따뜻함이 실종되가고 있는것 같습니다.
그 와중에 묵묵히 의사로서의 소명을 다하는 의사들은 어딜가나 환자들이 따르는 것은 당연하다 생각합니다.
"40년 이상 환자를 진료하고 있는 시글러 박사는 지금도 왕진을 다닌다. 그의 명함에는 휴대전화 번호와 집 전화번호가
함께 적혀 있다. 환자들이 원할 때 언제든지 연락이 닿을수 있도록 하기 위해서다." - 환자에게 먼저 다가서려고 하는 모습이
참 인상 깊었습니다.
[9.99933322e-01 6.66780556e-05] 선생님 안녕하세요?
  요즘 아들의 병세는 많이 좋아져 병이 있는 지 없는 지 모를 정도로 하루 하루를 무탈하게 잘 지내고 있습니다.
    어떤 날은 갑자

[0.66600502 0.33399498] 선생님 !오늘 대구에 가신다 했는데  글 올립니다.
아들은  강박증이 생기면 본인이 반복 행동을 하다가
성에차지 않으면  저를  문밖에 나가라 들어와를 한시간씩
시켰는데 항정신약물로는 치료가 힘든가요?
제가 이런 행동으로는  해소가 안되니 참으라고 하면
욕하고 화를 내었어요.
본인도 얼굴을 찌프리며 하는거보면 하고 싶지 않은데
제어가 안되나봐요.
길을 가다 다시뒤로 돌아갔다 앞으로 갔다하는건 정신적문제인가요?
강박증세 때문인가요?
오늘은 질문이 많았네요....
   
[9.99993611e-01 6.38890349e-06] 존경하는 선생님!!! .
추워지는 날씨에 건강하게 잘 보내 시는 지요?
저희 아이는 선생님 덕분에 너무 잘 지내고 있답니다.
이곳에 가끔 들어오면서 인사글을 남겨야지 하면서도 자꾸 미루다가 오늘에야 글을 올립니다.
선생님이 안계셨으면 저희 아이는 어떻게 되었을까을 생각하면 정말 아찔합니다.
정말 위대한 일을 하고 계십니다. 사람들을 다시 태어나게 하시어 생명을 다시 주시는 일이지요.
어떻게 감사한 마음을 표현할 길이 없습니다..하나님만이 아실겁니다.
  선생님 께서 처방해주신 아빌리 파이 를 2.5~3  미리 먹으면서 잘 지내고 있어요.
봄 3월 부터 시작해서 5 미리와 2.5 미리를 왓다 갓다 하면서 잘 지내고 잇어요.
시간이 지나면서 안 좋은 증상 들이 조금씩 여터지는것을 느낀답니다.
반짝이는 눈과 밝은 얼굴과 엄마를 도와 주는 손놀림과 마음 씨들이 점점 예전과 비슷하게 하고 있어요.
지금은 내년에 복학을 생각하고 있습니다.
학교에 너무도 돌아 가고 싶어 하고 있습니다.
예전 처럼 잘 할 자신을 아직 없지만  할려는 의욕은 많아요.
아직 기억력이 좋질 않아요.전에는 암기력이 정말 좋았는데요.
,선생님 정말 감사합니다.!!!!
한 번도 뵙적도 없지만 마치  당신의 환자인 양 새벽도 마다 안으시고 상담글 답글 주시고 ...
제가 죽어도 잊지 못할 은인이십니다.
항상 선생님을 생각하면 눈물이 납니다.

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.



[9.9999990e-01 1.0000001e-07] psyfree 상담실
  아들나이 28세 체중80K  키 177.5
밥을 먹자마자 바로 드러누어 눕자마자 잠들고 피곤해하며 자신도 흥미있는 일이없어 그렇다는 핑계인지를 대며 의욕없어 하며 잠만 계속 자고 또자고 한없이 자기만하고 제가 모든일을 제쳐놓고 서둘러서 데리고 나가지 않는한 산책도 안하며 그러기를 40일을 지켜보다가 제가 서둘러 2주간 저와 같이 택시회사
세차장에서 햇빛쐬며 3시부터7시까지 차를 닦았어요 약한 엄마가 본인을 위해 혼자할일을 둘이 나누어서 하니
고마워하며 근로의 자신감을 갖게 되었어요 둘이해도 1인하는임금이라 얼마 되지는 않았지만 지금을 있게한 너무 고마운 직장이었어요 그리고 바로 집앞 대형마트 구인광고에 면접을 보고 3일째
공산품코너 정리직원으로 대표가 하던 일을 나누어 배우고 있어요 고맙게도 차근차근히 처음부터 기대하지않고
가르키겠다고 염려하지말고 집에서도 많은 격려해주라고 해서 집에 큰 경사가 난듯 모자가 기뻐하고 있답니다
4년간 약복용중 단약으로 짧게 1~2주 혹1달내지 길면 2달여러차례(7~8회) 입원경헙이 있었고 최근 길게
6개월씩 이어두번 1년간 입원했었고 퇴원후 사회복귀시설에서 1년정도 생활을
하다가 5월1일부터 다시 집으로 들어와 생활하던차입니다 처음생각과는 달리 계속 40일간 자고 또 자는 아들을 지켜보며
제가 일을 해야하기땜에 직장에 나기기도 그렇고 함께 시간을 보내며 운동하기도 귀찮아 해서 자전거를 샀는데 그것도
안타네요 생각끝에 몸을 움직이는 세차일을 구해 같이 즐겁게 다녔습니다 지금 마트일이 9시 출근해서 밤10시반까지 근무인데
다행히 집에서 1~2분거리여서 점심 저녁식후 집에 다녀갈정도이고 직원들이 다 유순하고 부드러워서 대표는 특히 자상해서
배우고 일하는 재미에 피곤해도 잘 적응하고 있어요 마음이 즐겁다고 하네요 진종일 자다가 아무리 재미있다고 해도 피곤도가 25~30%라고 하는데 안스러워 권선생님카페 생각이 나서 아까 선생님과 통화도 하고 아들 퇴근후 건

[9.9999990e-01 1.0000001e-07] 28세/여 160, 64, 조현병, 설피딘400mm/ 재발 무, 1700번글

안녕하세요^^

지난주에 재발징조가 보여 설피딘 200에서 400으로
증량한 환자 동생입니다.
현재 지연성운동장애를 깨끗이 없애기 위해 설피딘복용중에 있고 현재 걸음걸이가 많이 자연스러워지고, 걸을 때 팔을 흔들면 힘없이 지마음대로 놀던 손이 힘을 찾은 듯 합니다

지연성운동장애는 어느정도 극복 된 듯 하나,
재발징조가 자꾸 보여 걱정이네요
제가 어학연수 간 사이 단약을 한 적이 있었는데,
그때 지금처럼 이랬다고 엄마가 말씀하시더라구요
입을 모으는 것과 자꾸 혼자 웃는 현상이요

지금 400mm로 증량한지 8일정도 밖에 안되서
더 지켜봐야겠지만 그래도 기록해봅니다.

지난 진료에 말씀 드렸던 입모으고 한번씩 웃는거 외엔 별 다른 증상은 없구요
예전보다 다 좋습니다
말하는거 행동하는게 많이 차분하구요
의지없던 것도 많이 좋아지고, 노력하는 것 같습니다
물론 우리가 시켜야 하는 부분이 많지만, 스스로 하는 모습도 가끔 보입니다
낮병원에 활동을 성실히 잘 하고 있구요
이제 신앙생활외에 피아노학원을 일주일에 한번 나가려고합니다. (피아노는 악보도 잘 읽고 집중해서 잘 칩니다)
일상생활에 지장 갈 것은 없지만
엄마가 단약했을 때 증상이라고 하니 한번 적어봅니다
(저는 단약 후 증상을 못 봤었기에..)

그리고 웃는 것 자체가 마음대로 안되는 듯 하네요
저도 정색하면서 하지말라고도 해보고
웃는 이유가 타당하지 않아 자꾸 되물어보니 화를 내네요
일단 강요하기보단 조용히..지켜봐야할 것 같습니다..

마지막으로 약은 보통 9시나 10시에 복용하구요
잠드는 시간은 규칙적이진 않고
11시에 잘 때도 잇고 12시,1시 넘어서 잘때도 있어요
그래도 평균7~8시간 정도 자는 것 같아요

선생님~ 팔 다치신거 빨리 쾌유하시길바래요~^^ *
항상 건강하세요!!!!^^
[9.9999990e-01 1.0000001e-07] psyfree 상담실
psyfree 

[9.99998688e-01 1.31164924e-06] 안녕하세요-?
어머니께서 이제 퇴원한지 9일되었습니다.
(ㅇ ㅎ ㄹ 환자 분입니다.)
  약도 거부하지않으시고 잘 복용하고 계시고,
다른 정신병 증상은 보이시지 않은데,
잠이 오다가도
자기전에
정신과약을 복용하고 난 후부터
계속 안절부절 하시고
화장실에 계속왔다갔다하시고
누우면 몸이 떨린다고 잠을 못주무셨습니다.
그래서 한차례 상담했었고
잠을 못 주무실때 마다 솔리안 200mg+디아제팜 10mg 반봉지 더 복용했었는데도
잠을 못 잡니다.
  현재
솔리안 400mg+벤즈 1mg+디아제팜 10mg
복용중이고
잠을 못 주무실때 마다 솔리안 200mg+디아제팜 10mg 반봉지 더 복용하고 있습니다.
오늘 까지 합쳐서 4일 가량 뜬눈으로 잠을 지새우셨습니다..
하루에 한,두시간 자는게 다입니다.
[9.9999990e-01 1.0000001e-07] psyfree 상담실
psyfree 님은 정신과 전문의로서 [정신분열병을 이겨낸 사람들]의 저자입니다.
현 근무처는 3월1일부터 의성효도요양병원(해안의료재단 소속, 054-834-6660, 경북 의성군 의성읍 원당리 1137-18)에 등록되어 외래진료만 가능합니다. 주 5일 근무라 실제 진료는 3월4일 월요일부터 시작되겠습니다.
입원진료는 법인체에서 준비중인 海眼병원(054-833-6000, 경북 의성군 의성읍 철파리 270-24) 개설이 3월11~18일 사이에 허가가 나는대로 시작되고, 해안병원 개설 이후는 요양병원에서 진료는 없어집니다.
상담하시는 분은 나이 / 성별, 키와 체중 및 체중 변화, 진단명, 복용하고 있는 약명 / 용량, 재발 유무, 이전 상담글 번호호를 기재해주시기 바랍니다.
  2월25일 퇴원. 잠 (새벽2시반~4시) 혼자웃어는 모습을 보여 왜 웃냐 물으니 아니 라고만 함. 핸드폰을 전달함.
2월26일 잠 (새벽2시반시~4시) 핸드폰 게임 여러차래에 걸쳐 (짧은 시간에 만원, 이만원, 오만원 총 21만원 결재,)
2월27일 아버지 말로는 잠을 많이 

In [47]:
import dill
wd = "./"
with open(wd + "schizophrenia_svm.model","wb") as f:
    dill.dump(ml,f)

In [48]:
model = dill.load(open("./schizophrenia_svm.model","rb"))
# y_pred =model.predict(all_list)
# accuracy = accuracy_score(binary_y, y_pred)
# print("Accuracy: %.2f%%" % (accuracy * 100.0))

-  ADHD

In [42]:
from sklearn.svm import SVC
ml = SVC(kernel='linear', C=1.0, random_state=0, probability=True)
ml.fit(x_train,y_train)

SVC(C=1.0, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto', kernel='linear',
  max_iter=-1, probability=True, random_state=0, shrinking=True, tol=0.001,
  verbose=False)

In [22]:
y_pred = ml.predict(x_train)

In [23]:
from sklearn.metrics import accuracy_score
print('총 테스트 개수: %d, 오류개수: %d' %(len(y_train), (y_train != y_pred).sum()))
print('정확도: %.2f' %accuracy_score(y_train, y_pred))

총 테스트 개수: 12962, 오류개수: 3386
정확도: 0.74


In [24]:
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
print('총 테스트 개수: %d, 오류개수: %d' %(len(y_train), (y_train != y_pred).sum()))
print('정확도: %.2f' %accuracy_score(y_train, y_pred))
print('f1_score : %.2f' %f1_score(y_train, y_pred, average='macro'))

총 테스트 개수: 12962, 오류개수: 3386
정확도: 0.74
f1_score : 0.67


In [25]:
for i in range(0,len(y_pred),1):
    print(y_pred[i])

0
1
0
0
0
0
0
0
1
1
1
0
1
0
0
0
0
1
1
0
1
0
0
0
0
0
0
0
0
1
0
1
1
1
1
1
0
1
0
0
0
0
0
0
0
0
1
0
0
0
0
0
1
1
1
1
1
1
0
0
0
1
1
1
0
0
1
0
0
1
1
0
0
0
1
0
0
0
0
0
0
0
1
0
0
1
0
0
1
0
0
0
0
1
0
1
0
0
0
0
0
1
1
1
0
1
1
0
0
1
0
0
0
0
1
0
1
1
0
0
0
1
0
0
1
0
0
1
1
0
0
0
1
0
0
1
1
0
0
0
0
0
1
0
1
1
1
0
1
1
0
1
1
1
1
0
1
0
0
0
1
1
1
0
0
0
0
0
0
1
1
1
1
0
1
0
0
1
1
0
1
1
1
0
1
0
1
1
0
1
0
0
0
1
0
1
1
0
0
0
0
0
1
0
0
1
0
0
0
1
1
0
1
0
0
1
0
1
1
0
1
0
1
0
0
0
0
0
1
0
0
0
0
1
0
1
0
1
1
1
0
1
1
0
0
0
1
0
1
1
1
0
0
1
0
0
0
0
1
0
1
1
1
0
0
1
0
0
1
0
1
1
0
0
0
1
1
1
1
0
1
0
0
1
0
1
1
0
0
0
1
0
0
1
1
0
1
0
0
1
0
0
0
0
1
0
1
0
0
1
1
1
0
0
0
1
0
0
1
0
1
0
0
0
1
1
0
1
0
0
0
0
1
0
1
1
1
0
0
0
1
0
0
1
1
1
0
1
0
1
1
1
1
1
0
0
0
1
0
0
0
1
1
0
1
0
1
0
0
1
0
0
0
1
0
1
0
1
1
1
1
0
1
0
0
0
0
1
0
0
1
0
1
0
0
1
1
1
1
1
1
1
1
1
0
1
1
1
0
0
0
1
0
0
0
1
1
0
0
0
1
1
1
0
1
1
1
1
1
0
1
0
0
1
1
0
0
1
1
0
1
0
0
0
0
1
0
0
0
1
0
0
0
0
1
0
0
0
0
0
0
0
0
1
0
1
0
1
1
1
0
1
0
0
0
0
0
0
1
1
0
0
0
1
0
0
1
0
0
1
1
0
0
1
1
1
1
1
0
1


1
1
0
1
1
1
1
0
0
1
1
1
0
0
1
1
1
0
1
1
1
1
1
1
1
1
0
1
1
1
1
1
0
0
1
1
1
1
1
1
1
0
1
0
1
1
0
1
1
1
1
0
1
1
1
1
1
1
1
1
1
1
1
1
0
1
1
1
1
1
1
1
1
0
1
1
1
1
0
0
0
1
1
0
0
1
1
1
1
1
1
0
1
1
0
1
1
1
1
1
1
1
1
1
0
0
1
1
1
1
1
1
0
0
1
1
1
1
0
1
1
1
1
1
0
1
1
1
1
1
1
1
0
1
0
1
1
1
1
1
1
1
1
1
1
1
0
0
1
1
1
1
1
1
1
0
0
1
1
1
1
1
0
0
1
1
0
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
0
1
1
1
1
1
0
0
0
1
1
1
0
1
1
1
1
0
1
1
1
1
1
1
0
1
1
1
1
1
1
1
1
1
1
1
1
1
0
1
1
1
1
1
1
1
0
1
1
1
0
1
1
1
1
1
1
1
1
1
1
0
1
0
1
1
0
1
1
1
1
1
0
1
1
1
1
1
1
1
1
0
0
0
0
1
1
1
1
0
1
1
1
1
1
1
1
1
1
1
1
0
1
0
0
1
1
1
1
1
1
0
1
0
1
1
1
1
1
0
0
1
1
0
1
1
1
1
1
1
1
1
1
0
1
1
1
1
1
0
0
1
1
0
1
0
1
1
1
0
0
1
1
1
0
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
0
0
1
1
1
0
1
1
1
0
1
1
1
0
1
0
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
0
1
1
1
0
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
0
1
1
1
1
1
1
1
1
1
1
1
1
1
1
0
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
0
1
1
1
1
1
1
1
1
1
1
1
1


1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
0
1
1
0
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
0
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


In [43]:
import dill
wd = "./"
with open(wd + "adhd_svm.model","wb") as f:
    dill.dump(ml,f)

- 우울증

In [36]:
from sklearn.svm import SVC
ml = SVC(kernel='linear', C=1.0, random_state=0, probability=True)
ml.fit(x_train,y_train)

SVC(C=1.0, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto', kernel='linear',
  max_iter=-1, probability=True, random_state=0, shrinking=True, tol=0.001,
  verbose=False)

In [32]:
y_pred = ml.predict(x_train)

In [33]:
from sklearn.metrics import accuracy_score
print('총 테스트 개수: %d, 오류개수: %d' %(len(y_train), (y_train != y_pred).sum()))
print('정확도: %.2f' %accuracy_score(y_train, y_pred))

총 테스트 개수: 17700, 오류개수: 5107
정확도: 0.71


In [31]:
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
print('총 테스트 개수: %d, 오류개수: %d' %(len(y_train), (y_train != y_pred).sum()))
print('정확도: %.2f' %accuracy_score(y_train, y_pred))
print('f1_score : %.2f' %f1_score(y_train, y_pred, average='macro'))

총 테스트 개수: 17700, 오류개수: 5107
정확도: 0.71
f1_score : 0.66


In [32]:
for i in range(0,len(y_pred),1):
    print(y_pred[i])

0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


0
0
1
1
1
0
1
1
1
1
1
1
0
1
0
0
1
1
1
1
1
0
0
1
1
1
1
0
0
0
0
1
1
0
0
1
1
0
0
0
0
0
0
0
0
1
0
0
1
1
1
1
0
1
1
1
0
1
0
0
0
1
0
1
0
0
1
0
1
1
0
1
1
0
0
1
1
1
1
0
0
1
1
0
0
1
1
0
0
0
1
1
0
0
0
1
1
1
0
0
0
0
1
0
1
1
0
0
1
1
0
0
1
1
0
0
1
1
1
0
0
1
1
1
0
0
1
0
0
1
0
0
0
0
0
0
1
0
0
1
0
1
1
1
0
1
0
1
0
1
0
1
0
0
1
0
1
1
0
0
1
0
0
0
0
1
0
0
1
0
1
0
0
1
1
0
1
1
1
0
0
1
1
0
0
1
0
0
1
1
0
1
1
1
1
0
1
0
0
1
0
1
0
0
0
1
0
1
1
0
1
0
0
0
1
1
1
0
0
1
0
0
0
0
0
0
0
1
0
0
0
1
1
0
1
1
1
0
0
0
0
0
0
0
0
1
1
0
1
1
1
1
0
1
1
0
1
1
0
0
0
0
1
1
1
1
1
1
0
1
1
0
0
0
0
0
1
0
0
0
0
0
1
1
0
0
1
0
0
1
0
1
0
0
0
0
1
1
0
1
1
0
1
1
0
1
0
0
0
0
1
1
1
0
1
0
1
0
1
0
0
1
1
1
0
0
1
0
0
1
1
0
1
0
0
1
1
1
1
0
0
0
0
1
0
0
0
0
0
1
1
1
1
0
0
1
1
0
0
0
1
0
1
1
1
1
0
0
1
1
1
0
0
1
0
0
1
1
0
0
1
0
0
1
1
0
1
0
1
1
1
1
0
1
1
1
0
0
1
0
0
0
1
0
0
1
1
1
1
1
0
0
0
1
1
0
1
0
1
0
1
0
1
0
1
0
0
1
1
1
1
0
0
0
0
1
0
0
1
1
0
1
0
1
0
0
1
1
0
0
1
0
0
0
1
1
1
1
1
0
1
1
0
1
1
0
1
0
0
1
0
1
1
0
1
1
0
0
0
0
0
1
1
1
0
0
0
0
1
0
1
0
0
1
0
0
0
0
0
0


In [39]:
import dill
wd = "./"
with open(wd + "sad_svm.model","wb") as f:
    dill.dump(ml,f)

In [37]:
y_pred_prob = ml.predict_proba(x_train)

# 모델 로드하여 측정

In [16]:
list([sad[0]])

[(1,
  '요양보호사라는 직업은 어떤가요?',
  '스트레스받으면서 알바하다가 한번 환청 비슷한거 들려서 힘들었었어요 요양보호사 직업도 많이 힘들까요..?',
  1)]

In [14]:
sad

[(1,
  '요양보호사라는 직업은 어떤가요?',
  '스트레스받으면서 알바하다가 한번 환청 비슷한거 들려서 힘들었었어요 요양보호사 직업도 많이 힘들까요..?',
  1),
 (2,
  '오랜만에 걸었어요.',
  '정말 오랜만에 땀나게 걸었어요. 넘 오랜만에 걸어서 중간중간 어지럽기는 했지만 동네 낙엽구경은 원없이 했네요. 땀도 오랜만에 흘리고요. 단풍구경 하시고 좋은저녁들 보내세요 ~~       ',
  1),
 (3,
  '잠이 안올때',
  '일하는동안 몸도 너무 힘들고 정신적으로도 지쳐서 돌거같은데 집에와서 자려니  잠이 안와서 한숨도 못자고 출근했는데 ...왜 너무 피곤하거나 스트레스가 심하거나 하면 잠이 안올까요 지쳐서 잠이라도 푹자고 나면 힘이라도 나고 우울도 덜할텐데 남들은 아무도 제마음을 몰라요 그냥 밖에서는 티를 낸적이 없고 가면 쓰고 살았어요 근데 쉬는날은 아무도 안만나고 집에 있는게 제일 편해요 사람도 싫고 나가는 것도 싫어진지 몇년되었어요 일은 어쩔수 없이 해야하니까 억지로 하고 있어요 ',
  1),
 (4,
  '돈만 쫒으며 억지로 일을 하려니 ',
  '돈만 쫒으며 돈때문에 하기싫은일 억지로 꾸역꾸역하다보니 불면증에 불안증에 우울에 하루하루가 지옥 같아요 그렇다고 딱히 하고싶은일도 할수 있을거 같은일도 없어요 그냥 아무것도 안하고 집에만 있고싶어요 미혼이니 일을 안할수는 없고 나이 더 먹기전에 집이라도 하나 있어야 겠고 마음은 급한데 몸은 천근만근 우울하고 사람대하는것도 너무 속으로는 싫어요 왜 태어나서 이고생인지 한살한살 더 먹을때마다 사는게 버겁고 힘드네요 그렇다고 결혼도 자신없고 이성격으로 버티지도 못할거 뻔한데 ...죽는것도 쉽지않고 그냥 안락사라도 허용된다면 곱게 사라지고 싶네요 지금 이순간에도 사는게 버겁기만 하고 나이드는것도 두려워요 앞으로 어떻게 먹고 살지도 막막하고 ㅜㅜ젊을때야 뭘해도 먹고살겠지만 나이들수록 할수 있는일도 많이 없을거같고 ...주위사람들이 제속마음이 이렇다는거 알면 놀랄거 같아요ㅜㅜ ',
  1)

In [18]:
import sen2vec
sen2vec = sen2vec.Sentence2Vec()


In [55]:
data = "ADHD 환자에게는 아래와 같은 성향이 있다고 함.

1) 좋아하는 것만 잘하고 나머진 다 못한다. 관심없다.
2) 잠 못 자면 지적활동, 언어 능력 유독 극감 
3) 밤에 머리가 더 잘 돌아간다
4) 악기 연주, 운동화끈, 젓가락질 등 작은 동작을 못한다
5) 성적은 나오는데 특정 과목은 답이 없다"
data = (0, '', data, 1)
data = list([data])
print(data)
test = sen2vec.get_vector(data)

[(0, '', '사실 난 졸라 부모님한테 가서 ha! in your face! 이지랄 떨고 싶다ㅋㅋㅋㅋㅋㅋㅋㅋ내가 의지박약이 아니였다고 시발 증세였다고 시발ㅋㅋㅋㅋㅋㅋㅋ', 1)]


In [51]:
import dill
model = dill.load(open("./adhd_svm.model","rb"))


In [56]:
predict = model.predict(test)
prob = model.predict_proba(test)
print(predict)
print(prob)

[1]
[[0.27847547 0.72152453]]
